In [1]:
# Genetic Algorithm Prototyping
# Going to be using this for the initial development of the scheduling algorithm.

In [2]:
# Make some sample data
from models import Classroom, Course, Teacher, ScheduledItem
from sampleData import SampleData

sampleData = SampleData()

rooms_json = sampleData.rooms
courses_json = sampleData.courses
teachers_json = sampleData.teachers

In [3]:
rooms = [
  Classroom(
    classroomId=room["classroomId"],
    name=room["name"],
    capacity=room["capacity"],
    type=room["type"],
    buildingId=room["buildingId"],
    isWheelchairAccessible=False,
    floor=room["floor"],
  ) for room in rooms_json
]

courses = [
  Course(
    courseId=course["courseId"],
    name=course["name"],
    description=course["description"],
    ectsCredits=course["ectsCredits"],
    department=course["department"],
    teacherId=course["teacherId"],
    sessionTypes=course["sessionTypes"],
    sessionsPerWeek=course["sessionsPerWeek"],
  ) for course in courses_json
]

teachers = [
  Teacher(
    teacherId=teacher["teacherId"],
    name=teacher["name"],
    email=teacher["email"],
    phone=teacher["phone"],
    department=teacher["departmentId"],
    needsWheelchairAccessibleRoom=False,
  ) for teacher in teachers_json
]

In [4]:
from scheduling import GeneticScheduler

# Example usage:
def run_scheduling():
    # Sample timeslots and days (would come from real data)
    timeslots = ["08:00-09:30", "09:40-11:10", "11:20-12:50", "13:30-15:00", "15:10-16:40"]
    days = ["Monday", "Tuesday", "Wednesday", "Thursday", "Friday"]
    
    # Create scheduler
    scheduler = GeneticScheduler(
        courses=courses,
        teachers=teachers,
        rooms=rooms,
        timeslots=timeslots,
        days=days,
        population_size=50,
        mutation_rate=0.1
    )
    
    # Run the genetic algorithm
    best_schedule, best_fitness = scheduler.run(generations=100)
    
    # Print results
    print(f"Best schedule fitness: {best_fitness}")
    if best_schedule:
        for item in best_schedule:
            print(f"Course: {item.courseName}, Room: {item.classroomId}, Day: {item.day}, Time: {item.timeslot}")
    
    return best_schedule


res = run_scheduling()

Room type conflict: lecture != lab
Room type conflict: lab != lecture
Room type conflict: lecture != lab
Room type conflict: lecture != lab
Room type conflict: lecture != lab
Room type conflict: lab != lecture
Room type conflict: lecture != lab
Room type conflict: lab != lecture
Room type conflict: lecture != lab
Room type conflict: lab != lecture
Room type conflict: lecture != lab
Room type conflict: lab != lecture
Room type conflict: lecture != lab
Room type conflict: lecture != lab
Room type conflict: lab != lecture
Room type conflict: lecture != lab
Room type conflict: lecture != lab
Room type conflict: lecture != lab
Room type conflict: lab != lecture
Room type conflict: lab != lecture
Room type conflict: lecture != lab
Room type conflict: lecture != lab
Room type conflict: lab != lecture
Room type conflict: lecture != lab
Room type conflict: lab != lecture
Room type conflict: lecture != lab
Room type conflict: lecture != lab
Room type conflict: lecture != lab
Room type conflict: 

In [5]:
rooms_dict = {room.classroomId: room for room in rooms}

In [6]:
import pandas as pd

def visualize_schedule(schedule, days, timeslots):
    """
    Visualize the schedule in a tabular format using pandas DataFrame
    Args:
        schedule: List[ScheduledItem] - The schedule to visualize
        days: List[str] - Days of the week
        timeslots: List[str] - Available timeslots
    """
    # Create empty timetable grid
    timetable = {day: {timeslot: "Free" for timeslot in timeslots} for day in days}
    
    # Fill in the timetable with scheduled items
    for item in schedule:
        if item.day in timetable and item.timeslot in timetable[item.day]:
            room = rooms_dict[item.classroomId]
            timetable[item.day][item.timeslot] = f"{item.courseName} ({room.name + ' (' + room.type + ')'})" + (
                " (Invalid)" if not item.is_valid_hard else ""
            )

    
    # Convert to pandas DataFrame for better visualization
    df = pd.DataFrame(timetable)
    df.index.name = 'Timeslot'
    
    # Print the timetable
    return df

# Example usage with the run_scheduling function
def run_scheduling_with_visualization():
    # Sample timeslots and days (would come from real data)
    timeslots = ["08:00-09:30", "09:40-11:10", "11:20-12:50", "13:30-15:00", "15:10-16:40"]
    days = ["Monday", "Tuesday", "Wednesday", "Thursday", "Friday"]
    
    # Create scheduler
    scheduler = GeneticScheduler(
        courses=courses,
        teachers=teachers,
        rooms=rooms,
        timeslots=timeslots,
        days=days,
        population_size=50,
        mutation_rate=0.1
    )
    
    # Run the genetic algorithm
    best_schedule, best_fitness = scheduler.run(generations=100)
    
    # Print results
    print(f"\nBest schedule fitness: {best_fitness}")
    if best_schedule:
        df = visualize_schedule(best_schedule, days, timeslots)
        # Optionally return the DataFrame for further analysis
        return best_schedule, df
    
    return best_schedule, None

# Run the scheduling with visualization
res, schedule_df = run_scheduling_with_visualization()
schedule_df

Room type conflict: lecture != lab
Room type conflict: lecture != lab
Room type conflict: lab != lecture
Room type conflict: lecture != lab
Room type conflict: lecture != lab
Room type conflict: lab != lecture
Room type conflict: lecture != lab
Room type conflict: lecture != lab
Room type conflict: lab != lecture
Room type conflict: lecture != lab
Room type conflict: lecture != lab
Room type conflict: lab != lecture
Room type conflict: lecture != lab
Room type conflict: lecture != lab
Room type conflict: lecture != lab
Room type conflict: lab != lecture
Room type conflict: lecture != lab
Room type conflict: lab != lecture
Room type conflict: lecture != lab
Room type conflict: lab != lecture
Room type conflict: lecture != lab
Room type conflict: lab != lecture
Room type conflict: lecture != lab
Room type conflict: lecture != lab
Room type conflict: lecture != lab
Room type conflict: lecture != lab
Room type conflict: lecture != lab
Room type conflict: lab != lecture
Room type conflict: 

Monday  \
Timeslot                                               
08:00-09:30   hci(lab/0) (NB111 (lecture)) (Invalid)   
09:40-11:10                                     Free   
11:20-12:50                                     Free   
13:30-15:00  comparch(lab/0) (NB115 (lab)) (Invalid)   
15:10-16:40                                     Free   

                                             Tuesday  \
Timeslot                                               
08:00-09:30                                     Free   
09:40-11:10  elec(lab/0) (NB113 (lecture)) (Invalid)   
11:20-12:50                                     Free   
13:30-15:00                                     Free   
15:10-16:40    se(lecture/0) (NB114 (lab)) (Invalid)   

                                          Wednesday  \
Timeslot                                              
08:00-09:30  hci(lecture/0) (NB114 (lab)) (Invalid)   
09:40-11:10                                    Free   
11:20-12:50                                    Free   
13:30-15:00  web(lecture/0) (NB115 (lab)) (Invalid)   
15:10-16:40                                    Free   

                                           Thursday  \
Timeslot                                              
08:00-09:30                                    Free   
09:40-11:10  web(lab/0) (NB111 (lecture)) (Invalid)   
11:20-12:50                                    Free   
13:30-15:00                                    Free   
15:10-16:40                                    Free   

                                                  Friday  
Timeslot                                                  
08:00-09:30                                         Free  
09:40-11:10        se(lab/0) (NB113 (lecture)) (Invalid)  
11:20-12:50                                         Free  
13:30-15:00                                         Free  
15:10-16:40  comparch(lecture/0) (NB115 (lab)) (Invalid)

In [7]:
res

[ScheduledItem(courseId='1', courseName='elec(lecture/0)', sessionType='lecture', teacherId='1', studentGroupId='G1', classroomId='5', timeslot='15:10-16:40', day='Tuesday', is_valid_hard=False, is_valid_soft=True),
 ScheduledItem(courseId='1', courseName='elec(lab/0)', sessionType='lab', teacherId='1', studentGroupId='G1', classroomId='3', timeslot='09:40-11:10', day='Tuesday', is_valid_hard=False, is_valid_soft=True),
 ScheduledItem(courseId='2', courseName='web(lecture/0)', sessionType='lecture', teacherId='2', studentGroupId='G1', classroomId='5', timeslot='13:30-15:00', day='Wednesday', is_valid_hard=False, is_valid_soft=True),
 ScheduledItem(courseId='2', courseName='web(lab/0)', sessionType='lab', teacherId='2', studentGroupId='G1', classroomId='1', timeslot='09:40-11:10', day='Thursday', is_valid_hard=False, is_valid_soft=True),
 ScheduledItem(courseId='3', courseName='hci(lecture/0)', sessionType='lecture', teacherId='3', studentGroupId='G1', classroomId='4', timeslot='08:00-0